# Similarity Search with Gensim

## Jupyter Notebook Test

Kód v [Jupyter Notebooku](https://jupyter.org/) můžete komentovat a dokumentovat pomocí [Markdown značkování](https://cs.wikipedia.org/wiki/Markdown).

Dále můžete přidávat buňky s Python kódem. Při stisku `Ctrl + Enter` je přitom kód vykonán a výstup zapsán do noteboku.

In [ ]:
print("Hello, World!")

## Nastavení logování

In [ ]:
import logging
#logging.basicConfig(format='%(asctime)s %(levelname)s %(filename)s:%(lineno)s %(message)s', level=logging.INFO)
logging.basicConfig(format='%(asctime)s %(levelname)s: %(message)s', level=logging.DEBUG)
logger = logging.getLogger(__name__)

## Potřebné moduly

In [ ]:
import sys, os
import re
import json
import gensim
from gensim.parsing.preprocessing import STOPWORDS
from gensim.utils import chunkize
from gensim import corpora, models, similarities
from smart_open import smart_open
from pprint import pprint, pformat

In [ ]:
# Hack Python to allow automatic recusive addition of dict keys, i.e. construction like:
#   d = ddict()
#   d['a']['b'] = 'c'
from collections import defaultdict
ddict = lambda: defaultdict(ddict)

## Načítání vstupních dat

Testovací data jsou v souboru `wiki-tabbed.tsv`.

In [ ]:
input_filepath = 'wiki-tabbed.tsv'


def parse_chunk(chunk):
    segment = json.loads(chunk)
    segment = re.sub("\s+", " ", segment, flags=re.MULTILINE).strip()
    return segment

def parse_input_line(line):
    chunks = line.strip().split('\t')
    title = parse_chunk(chunks[0])
    segments = []
    for (segment_title, segment_body) in chunkize(chunks[1:], 2):
        segments.append(u' '.join([parse_chunk(segment_title), parse_chunk(segment_body)]))
    return title, u' '.join(segments)

def yield_documents(input_filepath):
    """Iterate over input TSV file and yield parsed documents one-by-one"""
    with smart_open(input_filepath, 'rb') as f:
        for line in f:
            title, text = parse_input_line(line.decode('utf-8'))
            yield {
                'title': title,
                'content': text,
            }
            
# Jen debug výpis
for doc in yield_documents(input_filepath):
    logger.debug("%s: %s" % (doc['title'], doc['content'][:100] + '...'))

### Čištění dat

In [ ]:
# Jen ukázka jednoducného zpracování textu
test_text = 'Hello World! How is it going?! Nonexistentword, 21'

logger.debug("Simple preprocess:\n%s"
             % gensim.utils.simple_preprocess(test_text, deacc=True, min_len=2, max_len=15))
logger.debug("Simple preprocess with filtered out stop words:\n%s"
             % [token for token in gensim.utils.simple_preprocess(test_text, deacc=True, min_len=2, max_len=15) if token not in STOPWORDS])
logger.debug("Lemmatization:\n%s"
             % gensim.utils.lemmatize(test_text, min_length=2, max_length=15))
logger.debug("Lemmatization with filtered out stop words:\n%s"
             % gensim.utils.lemmatize(test_text, stopwords=STOPWORDS, min_length=2, max_length=15))

In [ ]:
def yield_tokenized_docs(input_filepath):
    """Iterate over input TSV file and yield processed token lists for every document
    
    For every document (line in TSV file) yields:
    { 'title': u'article title',
      'tokens': [u'list', u'of', u'tokens', u'of', u'the', u'article'] }
      
    English stop words are filtered out from the token list.
    """
    for doc in yield_documents(input_filepath):
        yield {
            'title': doc['title'],
            'tokens': [token
                       for token
                       in gensim.utils.simple_preprocess(
                           doc['title'] + doc['content'],
                           deacc=True, min_len=2, max_len=15)
                       if token not in STOPWORDS]
        }
        

# Jen debug výpis
for doc in yield_tokenized_docs(input_filepath):
    logger.debug("%s: %s" % (doc['title'], doc['tokens'][:20] + [u'...']))

## Indexování dat pomocí Gensim

### Vybudování slovníku

In [ ]:
# Pro slovník budeme potřebovat jen seznamu seznamů tokenů, textové pojmenování dokumentů odřízenem
def yield_tokens(input_filepath):
    """Iterate over input TSV file and yield processed token lists for every document
    
    For every document (line in TSV file) yields:
    [u'list', u'of', u'tokens', u'of', u'the', u'article']
      
    English stop words are filtered out from the token list.
    """
    for doc in yield_tokenized_docs(input_filepath):
        yield doc['tokens']

# Jen debug výpis
logger.debug("\n" + pformat([token_list[:3] + [u'...'] for token_list in yield_tokens(input_filepath)]))

In [ ]:
dict_filepath = 'wiki-tabbed.dict'

dictionary = corpora.Dictionary(yield_tokens(input_filepath))
dictionary.save(dict_filepath)
print(dictionary)
print(dictionary.token2id)

### Konverze dokumentů na bag-of-words

Jen ukázka konverze dokumentu na vektor

In [ ]:
new_doc = "Rabbit is a favorite pet."
new_vec = dictionary.doc2bow(new_doc.lower().split())
print(new_vec)

Ve slovníku jsou jen slova 'rabbit' (id 1523) a 'favorite (id 2104), ostatní tak jsou ignorována

In [ ]:
for w in new_doc.lower().split():
    print("%s: %s" % (w, dictionary.token2id[w] if w in dictionary.token2id else '<not in dictionary>'))

Skutečné vybudování korpusu

In [ ]:
corpus_filepath = 'wiki-tabbed.mm'

corpus = [dictionary.doc2bow(token_list) for token_list in yield_tokens(input_filepath)]
corpora.MmCorpus.serialize(corpus_filepath, corpus)
print(corpus)

### TF-IDF transformace

In [ ]:
tfidf = models.TfidfModel(corpus)

In [ ]:
corpus_tfidf = tfidf[corpus]

# Jen debug výpis
logger.debug("\n" + pformat([doc[:4] + ['...'] for doc in corpus_tfidf[:3]] + ['...']))

### Příprava LSI modelu

In [ ]:
NUM_OF_TOPICS = 10

lsi = models.LsiModel(corpus_tfidf, id2word=dictionary, num_topics=NUM_OF_TOPICS)
corpus_lsi = lsi[corpus_tfidf]

In [ ]:
# Jen debug výpis
logger.debug("\n" + pformat(lsi.print_topics()))

In [ ]:
lsi_model_filepath = 'wiki-tabbed.model.lsi'

lsi.save(lsi_model_filepath)
# Později může být znovu načteno příkazem:
#   lsi = models.LsiModel.load(lsi_model_filepath')

Transformací je k dispozici více, ne jen LSI (a.k.a LSA), viz [`models.*` v API dokumentaci Gensim](https://radimrehurek.com/gensim/apiref.html).

## Podobnostní hledání pomocí Gensim

### Vybudování indexu pro vyhledávání

In [ ]:
index = similarities.MatrixSimilarity(lsi[corpus])

In [ ]:
index_filepath = 'wiki-tabbed.index'

index.save(index_filepath)
# Později může být znovu načteno příkazem:
#   index = similarities.MatrixSimilarity.load('/tmp/deerwester.index')

### Podobnostní vyhledávání

Stanovíme si dotaz (dokument), kterým se budeme dotazovat.

In [ ]:
query_doc = "Rabbits are the best pets."

Následně dotaz převedeme na vektor.

In [ ]:
query_vec_bow = dictionary.doc2bow(query_doc.lower().split())
query_vec_lsi = lsi[query_vec_bow]

# Jen debug výpis
logger.debug("\n" + pformat(query_vec_lsi))

Pomocí vektoru dotazového dokumentu provede podobnostní vyhledávání v našem indexu.

In [ ]:
sims = index[query_vec_lsi]

# Jen debug výpis
logger.debug("\n" + pformat(["document #%03d: similarity %f" 
                             % (document_number, document_similarity)
                             for document_number, document_similarity
                             in enumerate(sims)][:20] + ['...']))

In [ ]:
WANTED_TOP_N_DOCS = 10

# Vyber WANTED_TOP_N_DOCS nejpodobnějších dokumentů
top_resutls = ddict()
for document_number, document_similarity in sorted(enumerate(sims), key=lambda item: -item[1])[:WANTED_TOP_N_DOCS]:
    logger.debug("doc_id = %d; doc_sim = %f" % (document_number, document_similarity))
    top_resutls[document_number]['similarity'] = document_similarity
    
# K nejpodobějším dokumentů dohledej jejich názvy
top_doc_ids = [document_number for document_number in sorted(top_resutls)]
logger.debug("top_doc_ids = %s" % top_doc_ids)
for doc_id, doc in enumerate(yield_documents(input_filepath)):
    if doc_id == top_doc_ids[0]:
        top_resutls[doc_id]['title'] = doc['title']
        top_doc_ids = top_doc_ids[1:]
        if len(top_doc_ids) == 0:  # Už jsme našli názvy všech našich dokumentů
            break                  # Je tak zbytečné dále zdržovat s iterováním korpusu
            
# Vypiš nejpodobnější dokumenty:
print("Query document:\n\t%s" % query_doc)
print("Similar documents:")
for i, doc_id in enumerate(sorted(top_resutls, key=lambda n: -top_resutls[n]['similarity'])):
    print(u"\t#%-2d [doc_id %3d, similarity %f] %s" % (i + 1,
                                                       doc_id,
                                                       top_resutls[doc_id]['similarity'],
                                                       top_resutls[doc_id]['title']))